# Folium Plotting

In [3]:
import folium
from folium.map import Icon, Marker, Popup
from folium.plugins import MarkerCluster
import pandas as pd
import numpy as np

Loading up the datasets that I'll be using to plot

In [4]:
bike_count = pd.read_csv('../../../Desktop/datasets/NYC_bike_count.csv', parse_dates=True)
bike_count.dropna(inplace=True)
bike_count = bike_count[bike_count['Year']>2012]

In [5]:
NY_weather_2013 = pd.read_csv(
'https://www.wunderground.com/history/airport/KNYC/2013/1/1/CustomHistory.html\
?dayend=31&monthend=12&yearend=2013&req_city=&req_state=&req_statename=&reqdb.\
zip=&reqdb.magic=&reqdb.wmo=&format=1')

NY_weather_2014 = pd.read_csv(
'https://www.wunderground.com/history/airport/KNYC/2014/1/1/CustomHistory.html\
?dayend=31&monthend=12&yearend=2014&req_city=&req_state=&req_statename=&reqdb.\
zip=&reqdb.magic=&reqdb.wmo=&format=1')

NY_weather_2015 = pd.read_csv(
'https://www.wunderground.com/history/airport/KNYC/2015/1/1/CustomHistory.html\
?dayend=31&monthend=12&yearend=2015&req_city=&req_state=&req_statename=&reqdb.\
zip=&reqdb.magic=&reqdb.wmo=&format=1')

In [6]:
NY_merged_samp = pd.read_pickle('../../../Desktop/datasets/NY_merged_new_.pkl')
NY_merged_samp = NY_merged_samp[(NY_merged_samp['DATE'] > '12/31/2012') & (NY_merged_samp['BOROUGH'] != 0)]

In [8]:
bike_count['m_helmet_ratio'] = (bike_count['Male_Cyc_Helmet'] / bike_count['MaleCyc_Total'])
bike_count['f_helmet_ratio'] = (bike_count['Female_Cyc_Helmet'] / bike_count['FemaleCyc_Total'])
bike_count['total_helmet_ratio'] = (bike_count['Cycl_Helmet_all'] / bike_count['CyclistVolume'])
all_helmet_groupby = bike_count.groupby(['Year'], as_index=False)['total_helmet_ratio'].mean()
m_helmet_groupby = bike_count.groupby(['Year'], as_index=False)['m_helmet_ratio'].mean()
f_helmet_groupby = bike_count.groupby(['Year'], as_index=False)['f_helmet_ratio'].mean()
helmet_groupby = bike_count.groupby(['Year'], as_index=False)[['m_helmet_ratio', 'f_helmet_ratio']].mean()
bike_helmet_group = bike_count.groupby(['Year'], as_index=False)[['Male_Cyc_Helmet','Female_Cyc_Helmet',
                                                                  'MaleCyc_Total','FemaleCyc_Total','CyclistVolume']].sum()

In [9]:
bike_count_group = bike_count.groupby(['Location','Location_Lat','Location_Long'], as_index=False)['CyclistVolume'].sum()
bike_count_location_helmets = bike_count.groupby(['Location', 'Year'], as_index=False)['total_helmet_ratio'].sum()
bike_count_location_group = bike_count.groupby(['Location', 'Year'], as_index= False)['CyclistVolume'].sum()

bike_count_group = pd.DataFrame(bike_count_group)
bike_count_group.CyclistVolume = bike_count_group.CyclistVolume.astype(float, inplace=True)

### Plotting the different cycling count locations

In [10]:
stamen = folium.Map(location=[40.7347476, -73.9122528], zoom_start=11, tiles='Stamen Terrain')

for desc, y, x in bike_count_group[['Location','Location_Lat', 'Location_Long']].values:
    folium.CircleMarker(location=[y, x], popup=desc,color='red').add_to(stamen)

stamen

In [11]:
manhattan_df = NY_merged_samp[NY_merged_samp['BOROUGH'] == 'MANHATTAN']
brooklyn_df = NY_merged_samp[NY_merged_samp['BOROUGH'] == 'BROOKLYN']
staten_df = NY_merged_samp[NY_merged_samp['BOROUGH'] == 'STATEN ISLAND']
queens_df = NY_merged_samp[NY_merged_samp['BOROUGH'] == 'QUEENS']
bronx_df = NY_merged_samp[NY_merged_samp['BOROUGH'] == 'BRONX']

In [12]:
NY_folium_df = NY_merged_samp
NY_folium_df.rename(columns={'BOROUGH':'BoroughName'}, inplace=True)
NY_folium_df['Borough_folium'] = NY_folium_df['BoroughName'].map(lambda x: x.title())
NY_folium_df_group = NY_folium_df.groupby(['Borough_folium'])['injuries'].sum()
NY_folium_df_group

Borough_folium
Bronx            1014
Brooklyn         4460
Manhattan        3475
Queens           2199
Staten Island     104
Name: injuries, dtype: int64

### Plotting each borough and its associated cycling crash counts

In [14]:
NYC_geo = r'../Capstone/boroughs.geojson'
NYC_collisions = NY_folium_df_group

NY_COORDINATES = (40.6347476, -74.1122528)
# for speed purposes
locations = []

MAX_RECORDS = 1000
# create empty map zoomed in on San Francisco
map = folium.Map(location=NY_COORDINATES, zoom_start=10, tiles='cartodbpositron')

# add a marker for every record in the filtered data, use a clustered view

b = map.choropleth(geo_path=NYC_geo, data=NY_folium_df_group,
             columns=['Borough_folium', 'injuries'],
             key_on='properties.BoroName',
             fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
             legend_name='Number of cycling accidents')

h = folium.FeatureGroup(name='bike')
for each in NY_merged_samp[0:MAX_RECORDS].iterrows():
    location = ([each[1]['LATITUDE'],each[1]['LONGITUDE']])
    locations.append(location)

h.add_children(MarkerCluster(locations=locations))#, popups=popups))

map.add_children(h)
map

/anaconda/envs/dsi/lib/python2.7/site-packages/ipykernel/__main__.py:18: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.
